# Summary

# Imports

In [9]:
import os
import os.path as op
import pickle

import numpy as np
import scipy as sp
import scipy.stats
import pandas as pd
import sqlalchemy as sa

from IPython.display import display, HTML
import matplotlib.pyplot as plt

import qgrid
qgrid.nbinstall(overwrite=True)
qgrid.set_defaults(remote_js=True, precision=4)

from common import dat

In [10]:
import pandas as pd
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [11]:
import seaborn as sns
sns.set_context('notebook', font_scale=2)
sns.set_style('whitegrid')

In [12]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [13]:
%%javascript
var kernel = IPython.notebook.kernel;
var thename = window.document.getElementById("notebook_name").innerHTML;
var command = "theNotebook = " + "'"+thename+"'";
kernel.execute(command);

<IPython.core.display.Javascript object>

In [14]:
counts = 0
while True:
    try:
        print(theNotebook)
        break
    except NameError:
        time.sleep(5)
        counts += 1
        if counts > 10:
            break

harmonizome


# Load data

In [9]:
# Load drug info data

# az_dream
engine = sa.create_engine('mysql://strokach:@192.168.6.19:3306/az_dream')
drug_info_release_3 = pd.read_sql_table('drug_info_release_3', engine)
drug_to_cid = pd.read_sql_table('drug_to_cid', engine)

# az_dream_data
engine = sa.create_engine('mysql://strokach:@192.168.6.19:3306/az_dream_data')
all_cell_line_drug_pairs = pd.read_sql_table('DRUG_PAIRS_CL', engine)
drug_to_target = pd.read_sql_table('drug_to_target', engine)
drug_to_target_stitch = pd.read_sql_table('drug_to_target_stitch', engine)

# az_dream_data

training_gby_drug = pd.read_sql_table('training_gby_drug', engine)
training_gby_drugpair = pd.read_sql_table('training_gby_drugpair', engine)
training_gby_cell = pd.read_sql_table('training_gby_cell', engine)

In [20]:
drug_info_release_3.columns

Index(['ChallengeName', 'Target(Official Symbol)', 'HBA', 'cLogP', 'HBD', 'Lipinski', 'SMILES or PubChem ID', 'MW', 'AtomStereoCount', 'BondStereoCount', 'CID', 'CanonicalSMILES', 'Charge', 'Complexity', 'ConformerCount3D', 'ConformerModelRMSD3D', 'CovalentUnitCount', 'DefinedAtomStereoCount', 'DefinedBondStereoCount', 'EffectiveRotorCount3D', 'ExactMass', 'FeatureAcceptorCount3D', 'FeatureAnionCount3D', 'FeatureCationCount3D', 'FeatureCount3D', 'FeatureDonorCount3D', 'FeatureHydrophobeCount3D', 'FeatureRingCount3D', 'Fingerprint2D', 'HBondAcceptorCount', 'HBondDonorCount', 'HeavyAtomCount', 'IUPACName', 'InChI', 'InChIKey', 'IsomericSMILES', 'IsotopeAtomCount', 'MolecularFormula', 'MolecularWeight', 'MonoisotopicMass', 'RotatableBondCount', 'TPSA', 'UndefinedAtomStereoCount', 'UndefinedBondStereoCount', 'Volume3D', 'XLogP', 'XStericQuadrupole3D', 'YStericQuadrupole3D', 'ZStericQuadrupole3D', 'cids', 'targets', 'targets_bioentities', 'enzymes', 'enzymes_bioentities', 'transporters',
  

In [30]:
dat.print2("Number of drugs:", drug_info_release_3['ChallengeName'].drop_duplicates().size)
dat.print2("Number of targets:", drug_info_release_3['Target(Official Symbol)'].drop_duplicates().size)

Number of drugs:                                            119
Number of targets:                                          85


## Gene to drug

In [11]:
engine = sa.create_engine('mysql://strokach:@192.168.6.19:3306/az_dream')
sql_query = """\
SELECT distinct drug, hgnc_name 
FROM az_dream.drug_to_target
LIMIT 100000;
"""
drug_to_hgnc = pd.read_sql_query(sql_query, engine)

In [16]:
drug_to_hgnc.head(2)

drug hgnc_name
0  ADAM17    ADAM17
1     AKT      AKT1

In [14]:
len(drug_to_hgnc['drug'].drop_duplicates())

119

In [17]:
len(drug_to_hgnc['hgnc_name'].drop_duplicates())

1511

In [32]:
unique_drugs = drug_to_hgnc['drug'].drop_duplicates().tolist()
unique_genes = drug_to_hgnc['hgnc_name'].drop_duplicates().tolist()

In [35]:
engine = sa.create_engine('mysql://strokach:@192.168.6.19:3306/harmonizome')
sql_query = """\
SELECT *
FROM gene_attribute_edges
WHERE source in ('{}')
and target in ('{}')
""".format("', '".join(unique_genes), "', '".join(unique_drugs))
df = pd.read_sql_query(sql_query, engine)

In [66]:
engine = sa.create_engine('mysql://strokach:@192.168.6.19:3306/harmonizome')
sql_query = """\
SELECT *
FROM gene_attribute_edges
WHERE source in ('{}')
and target in ('{}')
and weight != 1
""".format("', '".join(unique_genes), "', '".join(unique_drugs))
dfxx = pd.read_sql_query(sql_query, engine)

In [67]:
dfxx

Empty DataFrame
Columns: [data_origin, source, source_type, source_desc, source_desc_type, source_id, source_id_type, target, target_type, target_desc, target_desc_type, target_id, target_id_type, weight]
Index: []

In [44]:
df.head()

data_origin source source_type source_desc source_desc_type source_id source_id_type   target target_type target_desc target_desc_type target_id target_id_type  weight
0  BIND Biomolecular Interactions  HNF4A     GeneSym        None             None      3172         GeneID     TYMS     GeneSym        None             None      7298         GeneID       1
1  BIND Biomolecular Interactions    MYC     GeneSym        None             None      4609         GeneID  CSNK2A1     GeneSym        None             None      1457         GeneID       1
2  BIND Biomolecular Interactions  HNF4A     GeneSym        None             None      3172         GeneID  CSNK2A1     GeneSym        None             None      1457         GeneID       1
3  BIND Biomolecular Interactions  HDAC3     GeneSym        None             None      8841         GeneID  CSNK2A1     GeneSym        None             None      1457         GeneID       1
4  BIND Biomolecular Interactions   AKT1     GeneSym        None             None       207         GeneID  CSNK2A1     GeneSym        None             None      1457         GeneID       1

In [53]:
df['target_type'].drop_duplicates().tolist()

['GeneSym',
 'Chemical',
 'Drug',
 'Word',
 'Ligand',
 'Metabolite',
 'Domain',
 'Pathway',
 'TF Name',
 'Biological Term']

In [55]:
df['target_desc_type'].drop_duplicates().tolist()

[None,
 'PubchemCID',
 'DrugBankID',
 'HMDB ACC',
 'UniprotAcc',
 'DomainID',
 'Pathway ID',
 'ZScore']

In [59]:
df[df['weight'] != 1]

Empty DataFrame
Columns: [data_origin, source, source_type, source_desc, source_desc_type, source_id, source_id_type, target, target_type, target_desc, target_desc_type, target_id, target_id_type, weight]
Index: []

In [64]:
df2 = df[['data_origin', 'source', 'target', 'target_type', 'target_desc', 'target_desc_type', 'weight']].copy()

In [93]:
sp.stats.spearmanr([None, None, 1], [1, None, 1])

SpearmanrResult(correlation=0.86602540378443871, pvalue=0.3333333333333332)

In [88]:
df.set_index(['data_origin', 'source']).pivot(columns='target')['weight'].T.corr()

data_origin                                                   BIND Biomolecular Interactions                                                                                                                                                                                                                                                                                                                                                                                                                                    BioGRID Protein-Protein Interactions                                                                                                                                                                                                                                                                                                                                                                                                                                                             \
source                                                                                  ABL1 AKT1 ATR AURKB BAD BAK1 BAX BBC3 BCL2L12 BCR BID BRCA1 CASP1 CASP3 CASP8 CAV1 CD44 CD59 CDC25A CDC25C CDH1 CDK2 CFLAR CHUK CTNNB1 DDX17 DDX5 DNMT1 DUT E2F1 E2F4 E2F5 EGF EGFR EIF3I EP300 ERBB2 ESR2 GSN H2AFX HDAC1 HDAC3 HNF4A HRK HSP90AA1 ITGB5 JUN KLK3 MDM2 MECP2 MSH2 MUC1 MYC PDGFRB PLCG1 PLK1 PTK2 RAD51 RB1 RELA RICTOR RPTOR SRC STAT1 STAT3 STAT5A STAT5B TFF1 TNFRSF10B TNFRSF1A TNFRSF1B TOP1 TOP2A TP53 WRN YWHAQ                                ABCB1 ABL1 ABL2 ACTA2 ACTC1 ADRM1 AHR AIFM1 AKT1 AKT1S1 AKT2 ALB ALK APAF1 APOD APOE APP APRT APTX  AR ARFGEF1 ARR3 ATM ATP2A3 ATP5A1 ATR ATXN2 AURKA AURKB AURKC AXL BAD BAK1 BANF1 BARD1 BAX BBC3 BCL2 BCL2L1 BECN1 BID BIN1 BIRC2 BIRC3 BIRC5 BLK BLM BNIP3 BRCA1 BRCA2 BTG3 BTK BUB1B BUB3 CA3 CALU CAPRIN1 CASP1 CASP3 CASP8 CASP9 CAV1 CBR1 CCNA1 CCND1 CCNH CCR5 CD19 CD4 CD44 CD46 CD59 CD79A CD86 CDC20 CDC25A CDC25C CDH1 CDK2 CDK4 CDK7 CDKN1A CDKN1B   
data_origin                                   source                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              
BIND Biomolecular Interactions                ABL1                                       NaN  NaN NaN   NaN NaN  NaN NaN  NaN     NaN NaN NaN   NaN   NaN   NaN   NaN  NaN  NaN  NaN    NaN    NaN  NaN  NaN   NaN  NaN    NaN   NaN  NaN   NaN NaN  NaN  NaN  NaN NaN  NaN   NaN   NaN   NaN  NaN NaN   NaN   NaN   NaN   NaN NaN      NaN   NaN NaN  NaN  NaN   NaN  NaN  NaN NaN    NaN   NaN  NaN  NaN   NaN NaN  NaN    NaN   NaN NaN   NaN   NaN    NaN    NaN  NaN       NaN      NaN      NaN  NaN   NaN  NaN NaN   NaN                                  NaN  NaN  NaN   NaN   NaN   NaN NaN   NaN  NaN    NaN  NaN NaN NaN   NaN  NaN  NaN NaN  NaN  NaN NaN     NaN  NaN NaN    NaN    NaN NaN   NaN   NaN   NaN   NaN NaN NaN  NaN   NaN   NaN NaN  NaN  NaN    NaN   NaN NaN  NaN   NaN   NaN   NaN NaN NaN   NaN   NaN   NaN  NaN NaN   NaN  NaN NaN  NaN     NaN   NaN   NaN   NaN   NaN  NaN  NaN   NaN   NaN  NaN  NaN  NaN NaN  NaN  NaN  NaN   NaN  NaN   NaN    NaN    NaN  NaN  NaN  NaN  NaN    NaN    NaN   
                    

In [61]:
df2['data_origin'].drop_duplicates().tolist()

['BIND Biomolecular Interactions',
 'BioGRID Protein-Protein Interactions',
 'CHEA Transcription Factor Targets',
 'CTD Gene-Chemical Interactions',
 'DIP Protein-Protein Interactions',
 'DrugBank Drug Targets',
 'ENCODE Transcription Factor Targets',
 'GeneRIF Biological Term Annotations',
 'Guide to Pharmacology Chemical Ligands of Receptors',
 'Guide to Pharmacology Protein Ligands of Receptors',
 'HMDB Metabolites of Enzymes',
 'HPRD Protein-Protein Interactions',
 'Hub Proteins Protein-Protein Interactions',
 'IntAct Biomolecular Interactions',
 'InterPro Predicted Protein Domain Annotations',
 'JASPAR Predicted Transcription Factor Targets',
 'KEA Substrates of Kinases',
 'KEGG Pathways',
 'MSigDB Cancer Gene Co-expression Modules',
 'MotifMap Predicted Transcription Factor Targets',
 'NURSA Protein-Protein Interactions',
 'PANTHER Biomolecular Interactions',
 'PID Biomolecular Interactions',
 'Pathway Commons Protein-Protein Interactions',
 'PhosphoSitePlus Substrates of Kinases

## Gene to cell line

In [ ]:
engine = sa.create_engine('mysql://strokach:@192.168.6.19:3306/az_dream')
sql_query = """\
SELECT distinct drug, hgnc_name 
FROM az_dream.drug_to_target
LIMIT 100000;
"""
drug_to_hgnc = pd.read_sql_query(sql_query, engine)

In [38]:
len(drug_to_hgnc)

2324

## Make sure nothing else

In [3]:
plt.plot([1,2,3])

In [ ]:
sql_query = """\
select *
from gene_attribute_edges

"""